In [295]:
from auxFuncs import *

In [296]:
print("...ok! Python3 loaded.")

...ok! Python3 loaded.


In [297]:
now = datetime.now().strftime("%m_%d_%Y_%H_%M_%S")
sourceDir = "/Users/jordan/ThesisMARL/SURPL-V2/JJ_Juypter/results"
fileOut = open(sourceDir + "/PPO.txt", "w+")
tfSBLogs = sourceDir + "/SBlogs"
tfEVLogs = sourceDir + "/EVlogs"
print(tfSBLogs)
print(tfEVLogs)
now

/Users/jordan/ThesisMARL/SURPL-V2/JJ_Juypter/results/SBlogs
/Users/jordan/ThesisMARL/SURPL-V2/JJ_Juypter/results/EVlogs


'02_09_2022_15_55_00'

In [298]:
%load_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [299]:
# ------------------------------
#       SMART BUILDING
# ------------------------------
class SmartBuildingEnv(Env):
    def __init__(self):
        self.viewer = None
        self.load = 0
        self.demand = []
        self.timeStep = 0
        self.deltaUtilization = 0
        self.penalty = 0
        self.action_space = None
        self.observation_space = None
        self.reset()
        
    def reset(self):
        # self.load = 0
        # MOVE TO 24 HOURS FOR INITAL RESULTS NOW THAT PRELIM RESULTS ESTABLISHED
        self.demand = [3, 1, 1]
        # self.demand = np.array([3,1,1])
        # self.demand = [3, 2, 1]
        # self.timeStep +=1 == self.demand[self.timeStep]
        self.timeStep = 0
        self.deltaUtilization = abs(self.demand[self.timeStep] - self.load)
        self.penalty = (self.deltaUtilization) ** 2
        self.action_space = Box(low=0, high=self.demand[self.timeStep], shape=(1,), dtype=float)
        # OBSERVATION SPACE CAN ALSO INCLUDE DEMAND CHARGE, TIME, ETC -> 1 INSUFFICIENT FOR MORE RESULTS
        self.observation_space = Box(low=0, high=self.deltaUtilization, shape=(1,), dtype=float)
        # return np.array(0)
        return np.array([0])
        # pass
        # return state
    
    def step(self, action):
        info = {}
        reward = 0
        done:bool = False
        self.load = action[0]

        print("SB stepping: ", round(action[0], 2))
        print("*"*25)
        print("*"*25)
        print("SB stepping: ", round(action[0], 2), file=fileOut)
        print("*"*25, file=fileOut)
        print("*"*25, file=fileOut)
        

        print("Timestep: ", self.timeStep)
        print("-"*5)
        print("Load: ", round(self.load, 2))
        print("Demand: ", self.demand[self.timeStep])
        print("Timestep: ", self.timeStep, file=fileOut)
        print("-"*5, file=fileOut)
        print("Load: ", round(self.load, 2), file=fileOut)
        print("Demand: ", self.demand[self.timeStep], file=fileOut)


        self.deltaUtilization = abs(self.demand[self.timeStep] - self.load)
        self.penalty = (self.deltaUtilization) ** 2
        
        observation = self.demand[self.timeStep]
        
        print("Penalty: ", round(self.penalty, 2))
        print("Delta ", round(self.deltaUtilization, 2))
        print("Observation: ", observation)
        print("-"*25)
        print("Penalty: ", round(self.penalty, 2), file=fileOut)
        print("Delta ", round(self.deltaUtilization, 2), file=fileOut)
        print("Observation: ", observation, file=fileOut)
        print("-"*25, file=fileOut)
        
        # STILL NEED PEAK DEMAND IN REWARD
        # HOW DO WE CONTRIBUTE TO THIS REWARD?
        reward = 0
        if self.load != 0:
            reward -= self.load + self.penalty
        else:
            reward -= self.load + 1 + self.penalty
            
        # REWARD CAN BE DIFFERENCE BETWEEN COSTS

        self.timeStep += 1
        done = True if self.timeStep > 2 else done
            
        
        return np.array([observation]), reward, done, info
    
    def render(self, mode="human"):
        screen_h = 600
        screen_w = 1000
        if self.viewer is None:
            self.viewer = rendering.Viewer(screen_w, screen_h, "SB")
            
        return self.viewer.render(return_rgb_array=mode == "rgb_array")
    
    def close(self):
        if self.viewer:
            self.viewer.close()
            self.viewer = None

# ------------------------------
#            EV 
# ------------------------------
class ChargingStationEnv(Env):
    def __init__(self):
        self.viewer = None
        self.load = []
        # self.required = []
        self.required = 2
        self.timeStep = 0
        self.totalReward = 0
        self.chargingDeadline = 2
        self.demandCharge = 0
        # self.time = 0
        # self.reward = 0
        self.action_space = None
        self.observation_space = None
        self.reset()
        
    def reset(self):
        # self.time = 0
        self.timeStep = 0
        self.totalReward = 0
        # self.required = [1, 1, 0]
        self.load = []
        self.chargingDeadline = 2
        self.required = 2
        # self.chargingDeadline = len(self.required) - 1
        # self.chargingDeadline = len(self.required) - 1
        # print("Charging deadline: ", self.chargingDeadline, file=fileOut)
        # self.load = sum([l for l in self.required])
        self.action_space = Box(low=0, high=1, shape=(1,), dtype=float)
        # INCREASE OBSERVATION SPACE IF TRAIN LOSS CURVE IS UNIMPRESSIVE
        self.observation_space = Box(low=0, high=self.required, shape=(1,), dtype=float)
    
        
        return np.array([0])
        # pass
        # return state
    
    def step(self, action):
        info = {}
        reward = 0
        done: bool = False
        self.load.append(action[0])
        # self.load = action[0]
        self.demandCharge = max(self.load)
        
        
        print("EV stepping: ", round(action[0], 2))
        print("*"*25)
        print("*"*25)
        print("EV stepping: ", round(action[0], 2), file=fileOut)
        print("*"*25, file=fileOut)
        print("*"*25, file=fileOut)
        
        
        print("Timestep: ", self.timeStep)
        print("-"*5)
        # print("Load: ", round(self.load, 2))
        print("Load: ", [round(i, 2) for i in self.load])
        # print("Required: ", self.required[self.timeStep])
        print("Required: ", self.required)
        print("Timestep: ", self.timeStep, file=fileOut)
        print("-"*5, file=fileOut)
        # print("Load: ", round(self.load, 2), file=fileOut)
        print("Load: ", [round(i, 2) for i in self.load], file=fileOut)
        # print("Required: ", self.required[self.timeStep], file=fileOut)
        print("Required: ", self.required, file=fileOut)
    
            
        # observation = self.required[self.timeStep] 
        observation = self.required - self.load[0]
        
        
        print("Observation: ", round(observation, 2))
        print("-"*25)
        print("Observation: ", round(observation, 2), file=fileOut)
        print("-"*25, file=fileOut)

        
        # reward -= self.load
        
        # REWARD ONLY NEEDS TO MAKE SURE REQUIRED ENERGY IS CHARGED IN A FLAT ENERGY CHARGE DISTRIBUTION DUE TO PRICE FOR NOW
        # MEET DEADLINE BY REQUIRED CHARGING AMOUNT (REQUIRED -> TOTAL ENERGY)
        # CAN STOP AND RESTART MODEL PER 24 HOURS FOR NOW -> CONVOLUTION (SLIDING WINDOW)
        
        
        if self.timeStep == self.chargingDeadline and sum([i for i in self.load]) < self.required:
            reward = -10
        # PROBABLY CAN'T HAPPEN BECAUSE CONSTRAINT
        # elif self.timeStep >= self.required and sum([i for i in self.load]) > self.required:
        #     reward = -10
        # elif self.timeStep <= self.required:
        #     reward -= self.load[self.timeStep]
            
        elif self.timeStep < self.chargingDeadline:
            reward -= self.load[self.timeStep]
        elif self.timeStep == self.chargingDeadline:
            reward -= self.load[self.timeStep] + 2*(self.demandCharge)
            
        #DOES NOT ACTUALLY CONVERGE BASED ON PREVIOUS EPOCH'S REWARD; 
        #   -> INSTEAD, REWARD IS TOO RANDOM AT BEGINNING OF EACH EPOCH SO THE 
        #       AGENT NEVER LEARNS THE PROPER POLICY
            
        self.timeStep += 1
        self.totalReward += reward
        done = True if self.timeStep > 2 else done
        
        print("Total Reward: ", round(self.totalReward, 2))
        print("-"*25)
        print("Total Reward: ", round(self.totalReward, 2), file=fileOut)
        print("-"*25, file=fileOut)
        
        
        return np.array([observation]), reward, done, info
    
    def render(self, mode="human"):
        screen_h = 600
        screen_w = 1000
        if self.viewer is None:
            self.viewer = rendering.Viewer(screen_w, screen_h, "EV")
            
        return self.viewer.render(return_rgb_array=mode == "rgb_array")
    
    def close(self):
        if self.viewer:
            self.viewer.close()
            self.viewer = None

In [300]:
SBenv = SmartBuildingEnv()
EVenv = ChargingStationEnv()
# env = DummyVecEnv([lambda: env])
# batch_size = 500
# ep_per_batch = 10 * batch_size
batch_size = 500
ep_per_batch = 10 * batch_size

In [301]:
model_SBE = PPO("MlpPolicy", SBenv, verbose=1, tensorboard_log=tfSBLogs)
model_CSE = PPO('MlpPolicy', EVenv, verbose = 1, tensorboard_log=tfEVLogs)
# model_SBE = PPO("MlpPolicy", SBenv, verbose=1)
# model_CSE = PPO('MlpPolicy', EVenv, verbose = 1)
print("Aggregating models...")
models = [model_SBE, model_CSE]
envs = [SBenv, EVenv]

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Aggregating models...


In [302]:
check_env(SBenv)

SB stepping:  2.73
*************************
*************************
Timestep:  0
-----
Load:  2.73
Demand:  3
Penalty:  0.07
Delta  0.27
Observation:  3
-------------------------
SB stepping:  2.63
*************************
*************************
Timestep:  1
-----
Load:  2.63
Demand:  1
Penalty:  2.67
Delta  1.63
Observation:  1
-------------------------
SB stepping:  2.88
*************************
*************************
Timestep:  2
-----
Load:  2.88
Demand:  1
Penalty:  3.52
Delta  1.88
Observation:  1
-------------------------
SB stepping:  1.88
*************************
*************************
Timestep:  0
-----
Load:  1.88
Demand:  3
Penalty:  1.25
Delta  1.12
Observation:  3
-------------------------
SB stepping:  2.47
*************************
*************************
Timestep:  1
-----
Load:  2.47
Demand:  1
Penalty:  2.16
Delta  1.47
Observation:  1
-------------------------
SB stepping:  0.01
*************************
*************************
Timestep:  2
-----


/Users/jordan/.pyenv/versions/3.7.11/envs/agentppo/lib/python3.7/site-packages/stable_baselines3/common/env_checker.py:273: UserWarning: We recommend you to use a symmetric and normalized Box action space (range=[-1, 1]) cf https://stable-baselines3.readthedocs.io/en/master/guide/rl_tips.html
  "We recommend you to use a symmetric and normalized Box action space (range=[-1, 1]) "
/Users/jordan/.pyenv/versions/3.7.11/envs/agentppo/lib/python3.7/site-packages/stable_baselines3/common/env_checker.py:279: UserWarning: Your action space has dtype float64, we recommend using np.float32 to avoid cast errors.
  f"Your action space has dtype {action_space.dtype}, we recommend using np.float32 to avoid cast errors."


In [303]:
check_env(EVenv)

EV stepping:  0.42
*************************
*************************
Timestep:  0
-----
Load:  [0.42]
Required:  2
Observation:  1.58
-------------------------
Total Reward:  -0.42
-------------------------
EV stepping:  1.21
*************************
*************************
Timestep:  1
-----
Load:  [0.42, 1.21]
Required:  2
Observation:  1.58
-------------------------
Total Reward:  -1.63
-------------------------
EV stepping:  1.15
*************************
*************************
Timestep:  2
-----
Load:  [0.42, 1.21, 1.15]
Required:  2
Observation:  1.58
-------------------------
Total Reward:  -5.19
-------------------------
EV stepping:  0.49
*************************
*************************
Timestep:  0
-----
Load:  [0.49]
Required:  2
Observation:  1.51
-------------------------
Total Reward:  -0.49
-------------------------
EV stepping:  1.52
*************************
*************************
Timestep:  1
-----
Load:  [0.49, 1.52]
Required:  2
Observation:  1.51
----

In [304]:
model_SBE.learn(total_timesteps=ep_per_batch, reset_num_timesteps=False, tb_log_name=tfSBLogs)

Logging to /Users/jordan/ThesisMARL/SURPL-V2/JJ_Juypter/results/SBlogs_0
SB stepping:  0.0
*************************
*************************
Timestep:  0
-----
Load:  0.0
Demand:  3
Penalty:  9.0
Delta  3.0
Observation:  3
-------------------------
SB stepping:  0.75
*************************
*************************
Timestep:  1
-----
Load:  0.75
Demand:  1
Penalty:  0.06
Delta  0.25
Observation:  1
-------------------------
SB stepping:  0.0
*************************
*************************
Timestep:  2
-----
Load:  0.0
Demand:  1
Penalty:  1.0
Delta  1.0
Observation:  1
-------------------------
SB stepping:  0.98
*************************
*************************
Timestep:  0
-----
Load:  0.98
Demand:  3
Penalty:  4.09
Delta  2.02
Observation:  3
-------------------------
SB stepping:  0.0
*************************
*************************
Timestep:  1
-----
Load:  0.0
Demand:  1
Penalty:  1.0
Delta  1.0
Observation:  1
-------------------------
SB stepping:  1.39
**********

In [305]:
obs = SBenv.reset() 

for i in range(batch_size):
    action, _states = model_SBE.predict(obs, deterministic=True)
    # action = env.action_space.sample()
    
    obs, reward, done, info = SBenv.step(action)
    # if ep_per_batch % 2000 == 0:
    # env.render()
    if done:
        obs = SBenv.reset()

SB stepping:  1.18
*************************
*************************
Timestep:  0
-----
Load:  1.18
Demand:  3
Penalty:  3.3
Delta  1.82
Observation:  3
-------------------------
SB stepping:  0.25
*************************
*************************
Timestep:  1
-----
Load:  0.25
Demand:  1
Penalty:  0.57
Delta  0.75
Observation:  1
-------------------------
SB stepping:  0.48
*************************
*************************
Timestep:  2
-----
Load:  0.48
Demand:  1
Penalty:  0.27
Delta  0.52
Observation:  1
-------------------------
SB stepping:  1.18
*************************
*************************
Timestep:  0
-----
Load:  1.18
Demand:  3
Penalty:  3.3
Delta  1.82
Observation:  3
-------------------------
SB stepping:  0.25
*************************
*************************
Timestep:  1
-----
Load:  0.25
Demand:  1
Penalty:  0.57
Delta  0.75
Observation:  1
-------------------------
SB stepping:  0.48
*************************
*************************
Timestep:  2
-----
Lo

In [306]:
# mean_reward, std_reward = evaluate_policy(model, env, n_eval_episodes=100, render=True)
mean_reward, std_reward = evaluate_policy(model_SBE, SBenv, n_eval_episodes=1000)

print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

/Users/jordan/.pyenv/versions/3.7.11/envs/agentppo/lib/python3.7/site-packages/stable_baselines3/common/evaluation.py:69: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  UserWarning,


SB stepping:  1.18
*************************
*************************
Timestep:  0
-----
Load:  1.18
Demand:  3
Penalty:  3.3
Delta  1.82
Observation:  3
-------------------------
SB stepping:  0.25
*************************
*************************
Timestep:  1
-----
Load:  0.25
Demand:  1
Penalty:  0.57
Delta  0.75
Observation:  1
-------------------------
SB stepping:  0.48
*************************
*************************
Timestep:  2
-----
Load:  0.48
Demand:  1
Penalty:  0.27
Delta  0.52
Observation:  1
-------------------------
SB stepping:  1.18
*************************
*************************
Timestep:  0
-----
Load:  1.18
Demand:  3
Penalty:  3.3
Delta  1.82
Observation:  3
-------------------------
SB stepping:  0.25
*************************
*************************
Timestep:  1
-----
Load:  0.25
Demand:  1
Penalty:  0.57
Delta  0.75
Observation:  1
-------------------------
SB stepping:  0.48
*************************
*************************
Timestep:  2
-----
Lo

In [307]:
model_SBE.save("results/PPO_" + "/SmartBuilding")

In [308]:
print("-"*50, file=fileOut)
print("-"*50, file=fileOut)

In [309]:
model_CSE.learn(total_timesteps=ep_per_batch, reset_num_timesteps=False, tb_log_name=tfEVLogs)

Logging to /Users/jordan/ThesisMARL/SURPL-V2/JJ_Juypter/results/EVlogs_0
EV stepping:  0.0
*************************
*************************
Timestep:  0
-----
Load:  [0.0]
Required:  2
Observation:  2.0
-------------------------
Total Reward:  0.0
-------------------------
EV stepping:  0.0
*************************
*************************
Timestep:  1
-----
Load:  [0.0, 0.0]
Required:  2
Observation:  2.0
-------------------------
Total Reward:  0.0
-------------------------
EV stepping:  0.5
*************************
*************************
Timestep:  2
-----
Load:  [0.0, 0.0, 0.5]
Required:  2
Observation:  2.0
-------------------------
Total Reward:  -10.0
-------------------------
EV stepping:  1.22
*************************
*************************
Timestep:  0
-----
Load:  [1.22]
Required:  2
Observation:  0.78
-------------------------
Total Reward:  -1.22
-------------------------
EV stepping:  1.1
*************************
*************************
Timestep:  1
-----


In [310]:
obs = EVenv.reset() 

for i in range(batch_size):
    action, _states = model_CSE.predict(obs, deterministic=True)
    # action = env.action_space.sample()
    
    obs, reward, done, info = EVenv.step(action)
    # if ep_per_batch % 2000 == 0:
    # env.render()
    if done:
        obs = EVenv.reset()

EV stepping:  0.46
*************************
*************************
Timestep:  0
-----
Load:  [0.46]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -0.46
-------------------------
EV stepping:  0.65
*************************
*************************
Timestep:  1
-----
Load:  [0.46, 0.65]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -1.11
-------------------------
EV stepping:  0.65
*************************
*************************
Timestep:  2
-----
Load:  [0.46, 0.65, 0.65]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -11.11
-------------------------
EV stepping:  0.46
*************************
*************************
Timestep:  0
-----
Load:  [0.46]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -0.46
-------------------------
EV stepping:  0.65
*************************
*************************
Timestep:  1
-----
Load:  [0.46, 0.65]
Required:  2
Observation:  1.54
---

In [311]:
# mean_reward, std_reward = evaluate_policy(model, env, n_eval_episodes=100, render=True)
mean_reward, std_reward = evaluate_policy(model_CSE, EVenv, n_eval_episodes=1000)

print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

EV stepping:  0.46
*************************
*************************
Timestep:  0
-----
Load:  [0.46]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -0.46
-------------------------
EV stepping:  0.65
*************************
*************************
Timestep:  1
-----
Load:  [0.46, 0.65]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -1.11
-------------------------
EV stepping:  0.65
*************************
*************************
Timestep:  2
-----
Load:  [0.46, 0.65, 0.65]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -11.11
-------------------------
EV stepping:  0.46
*************************
*************************
Timestep:  0
-----
Load:  [0.46]
Required:  2
Observation:  1.54
-------------------------
Total Reward:  -0.46
-------------------------
EV stepping:  0.65
*************************
*************************
Timestep:  1
-----
Load:  [0.46, 0.65]
Required:  2
Observation:  1.54
---

In [312]:
model_CSE.save("results/PPO_" + "/ChargingStation")

In [326]:
%tensorboard --logdir {tfSBLogs + "_0"}

Reusing TensorBoard on port 6007 (pid 26968), started 0:00:03 ago. (Use '!kill 26968' to kill it.)

In [327]:
%tensorboard --logdir {tfEVLogs + "_0"}

Reusing TensorBoard on port 6006 (pid 26793), started 0:00:21 ago. (Use '!kill 26793' to kill it.)

In [315]:

# %tensorboard --logdir {sourceDir + "/EVlogs"}

In [316]:
fileOut.close()